<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Objectifs" data-toc-modified-id="Objectifs-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Objectifs</a></span></li><li><span><a href="#Dev" data-toc-modified-id="Dev-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Dev</a></span></li><li><span><a href="#Industrialisation" data-toc-modified-id="Industrialisation-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Industrialisation</a></span><ul class="toc-item"><li><ul class="toc-item"><li><span><a href="#Script" data-toc-modified-id="Script-3.0.1"><span class="toc-item-num">3.0.1&nbsp;&nbsp;</span>Script</a></span></li></ul></li></ul></li><li><span><a href="#Analyse-de-la-feature" data-toc-modified-id="Analyse-de-la-feature-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Analyse de la feature</a></span><ul class="toc-item"><li><span><a href="#Stations-avec-le-plus-grand-nombre-de-non-prise-de-vélo-consécutif" data-toc-modified-id="Stations-avec-le-plus-grand-nombre-de-non-prise-de-vélo-consécutif-4.1"><span class="toc-item-num">4.1&nbsp;&nbsp;</span>Stations avec le plus grand nombre de non prise de vélo consécutif</a></span></li></ul></li></ul></div>

In [1]:
import pandas as pd

from vcub_keeper.reader.reader import *
from vcub_keeper.visualisation import plot_station_activity
from vcub_keeper.transform.features_factory import *

import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style('whitegrid')
%matplotlib inline

%load_ext autoreload
%autoreload 2

pd.options.display.max_rows = 500

## Objectifs

- Permettre de savoir depuis combien de temps un vélo n'a pas été pris par station. Plus ce nombre est grand plus il y a de chance que la station soit HS. Cf https://github.com/armgilles/vcub_keeper/issues/10
- Industrialisation de la function.
- Analyse de la feature

## Dev

In [6]:
activite = read_activity_vcub()

activite = get_transactions_out(activite)

In [7]:
activite['compteur'] = 1
activite['consecutive_no_transactions_out'] = \
    activite.groupby([(activite['transactions_out'] > 0).cumsum(),
                      'station_id'])['compteur'].cumsum() # 

activite['consecutive_no_transactions_out'] = \
    activite['consecutive_no_transactions_out'].fillna(0)

activite = activite.drop('compteur', axis=1)

In [9]:
activite[(activite['station_id'] == 1) & (activite.date >= "2017-07-10 09:04:04")].head(15)

gid  station_id type       name state  available_stand  available_bike  \
395   83           1  VLS  Meriadeck     1                0              20   
396   83           1  VLS  Meriadeck     1                0              20   
397   83           1  VLS  Meriadeck     1                0              20   
398   83           1  VLS  Meriadeck     1                0              20   
399   83           1  VLS  Meriadeck     1                0              20   
400   83           1  VLS  Meriadeck     1                1              19   
401   83           1  VLS  Meriadeck     1                0              20   
402   83           1  VLS  Meriadeck     1                0              20   
403   83           1  VLS  Meriadeck     1                0              20   
404   83           1  VLS  Meriadeck     1                0              20   
405   83           1  VLS  Meriadeck     1                1              19   
406   83           1  VLS  Meriadeck     1                2              18   
407   83           1  VLS  Meriadeck     1                2              18   
408   83           1  VLS  Meriadeck     1                2              18   
409   83           1  VLS  Meriadeck     1                2              18   

                   date  transactions_out  consecutive_no_transactions_out  
395 2017-07-10 09:04:04               0.0                                3  
396 2017-07-10 09:09:03               0.0                                4  
397 2017-07-10 09:14:06               0.0                                5  
398 2017-07-10 09:19:04               0.0                                6  
399 2017-07-10 09:24:04               0.0                                7  
400 2017-07-10 09:29:07               1.0                                1  
401 2017-07-10 09:34:05               0.0                                2  
402 2017-07-10 09:39:05               0.0                                3  
403 2017-07-10 09:44:04               0.0                                4  
404 2017-07-10 09:49:04               0.0                                5  
405 2017-07-10 09:54:05               1.0                                1  
406 2017-07-10 09:59:05               1.0                                1  
407 2017-07-10 10:04:05               0.0                                2  
408 2017-07-10 10:09:12               0.0                                3  
409 2017-07-10 10:14:11               0.0                                4

In [10]:
# Entre 2 stations différentes
activite[21610:21625]

gid  station_id type       name state  available_stand  available_bike  \
21610   83           1  VLS  Meriadeck     1               16               3   
21611   83           1  VLS  Meriadeck     1               17               2   
21612   83           1  VLS  Meriadeck     1               16               3   
21613   83           1  VLS  Meriadeck     1               15               4   
21614   83           1  VLS  Meriadeck     1               14               5   
21615   83           1  VLS  Meriadeck     1               14               5   
21616   83           1  VLS  Meriadeck     1               13               6   
21617   83           1  VLS  Meriadeck     1               14               5   
21618   83           1  VLS  Meriadeck     1               13               6   
21619   83           1  VLS  Meriadeck     1               13               6   
21620   84           2  VLS   St Bruno     1                7              13   
21621   84           2  VLS   St Bruno     1                7              13   
21622   84           2  VLS   St Bruno     1                7              13   
21623   84           2  VLS   St Bruno     1                7              13   
21624   84           2  VLS   St Bruno     1                7              13   

                     date  transactions_out  consecutive_no_transactions_out  
21610 2017-09-26 14:14:03               0.0                                5  
21611 2017-09-26 14:19:03               1.0                                1  
21612 2017-09-26 14:24:04               0.0                                2  
21613 2017-09-26 14:29:05               0.0                                3  
21614 2017-09-26 14:34:03               0.0                                4  
21615 2017-09-26 14:39:02               0.0                                5  
21616 2017-09-26 14:44:05               0.0                                6  
21617 2017-09-26 14:49:05               1.0                                1  
21618 2017-09-26 14:54:04               0.0                                2  
21619 2017-09-26 14:59:04               0.0                                3  
21620 2017-07-09 00:03:04               0.0                                1  
21621 2017-07-09 00:04:04               0.0                                2  
21622 2017-07-09 00:09:04               0.0                                3  
21623 2017-07-09 00:14:03               0.0                                4  
21624 2017-07-09 00:19:05               0.0                                5

## Industrialisation

In [12]:
def get_consecutive_no_transactions_out(data):
    """
    Calcul depuis combien de temps la station n'a pas eu de prise de vélo. Plus le chiffre est haut, 
    plus ça fait longtemps que la station est inactive sur la prise de vélo.
    
    Parameters
    ----------
    data : DataFrame
        Activité des stations Vcub avec la feature `transactions_out` (get_transactions_out)
    
    Returns
    -------
    data : DataFrame
        Ajout de colonne 'consecutive_no_transactions_out'
        
    Examples
    --------
    
    activite = get_consecutive_no_transactions_out(activite)
    """
    
    data['compteur'] = 1
    data['consecutive_no_transactions_out'] = \
        data.groupby([(data['transactions_out'] > 0).cumsum(),
                      'station_id'])['compteur'].cumsum()

    data['consecutive_no_transactions_out'] = \
        data['consecutive_no_transactions_out'].fillna(0)

    data = data.drop('compteur', axis=1)
    return data

In [13]:
activite = read_activity_vcub()

activite = get_transactions_out(activite)

In [14]:
activite = get_consecutive_no_transactions_out(activite)

#### Script 

In [16]:
from vcub_keeper.reader.reader import *
from vcub_keeper.transform.features_factory import *

In [18]:
activite = read_activity_vcub()

activite = get_transactions_out(activite)
activite = get_consecutive_no_transactions_out(activite)

In [20]:
activite.tail(10)

gid  station_id type    name state  available_stand  available_bike  \
3761870  176         174  VLS  Darwin     1                0              20   
3761871  176         174  VLS  Darwin     1                0              20   
3761872  176         174  VLS  Darwin     1                1              19   
3761873  176         174  VLS  Darwin     1                1              19   
3761874  176         174  VLS  Darwin     1                1              19   
3761875  176         174  VLS  Darwin     1                1              19   
3761876  176         174  VLS  Darwin     1                0              20   
3761877  176         174  VLS  Darwin     1                0              20   
3761878  176         174  VLS  Darwin     1                0              20   
3761879  176         174  VLS  Darwin     1                0              20   

                       date  transactions_out  consecutive_no_transactions_out  
3761870 2017-09-26 14:14:04               0.0                               16  
3761871 2017-09-26 14:19:03               0.0                               17  
3761872 2017-09-26 14:24:04               1.0                                1  
3761873 2017-09-26 14:29:05               0.0                                2  
3761874 2017-09-26 14:34:03               0.0                                3  
3761875 2017-09-26 14:39:02               0.0                                4  
3761876 2017-09-26 14:44:05               0.0                                5  
3761877 2017-09-26 14:49:05               0.0                                6  
3761878 2017-09-26 14:54:04               0.0                                7  
3761879 2017-09-26 14:59:04               0.0                                8

## Analyse de la feature

In [21]:
activite = read_activity_vcub()

activite = get_transactions_out(activite)
activite = get_consecutive_no_transactions_out(activite)

### Stations avec le plus grand nombre de non prise de vélo consécutif

In [34]:
grp_station = activite.groupby('station_id', as_index=False)['consecutive_no_transactions_out'].max()
grp_station = grp_station.sort_values('consecutive_no_transactions_out', ascending=0)

In [36]:
grp_station.head(10)

station_id  consecutive_no_transactions_out
136         137                            21620
34           35                            21620
92           93                            21620
75           76                            17164
103         104                             8074
46           47                             7775
24           25                             7575
159         160                             3953
118         119                             3490
154         155                             1939

**Certaines stations sont très inactives (travaux ?)**

In [50]:
station_id = 160
start_date = "2017-08-05"
end_date = "2017-08-07"
tt = plot_station_activity(activite, station_id=station_id, 
                      features_to_plot=['available_bike', 'available_stand',
                                        'consecutive_no_transactions_out'],
                      #start_date=start_date,
                      #end_date=end_date,
                      return_data=False
                     )

In [53]:
station_id = 155
start_date = "2017-07-25"
end_date = "2017-08-09"
tt = plot_station_activity(activite, station_id=station_id, 
                      features_to_plot=['available_bike', 'available_stand',
                                        'consecutive_no_transactions_out'],
                      start_date=start_date,
                      end_date=end_date,
                      return_data=True
                     )

In [54]:
tt[100:150]

gid  station_id  type           name state  available_stand  \
3333892  156         155  VLS+  Village 6 IUT     1               17   
3333893  156         155  VLS+  Village 6 IUT     1               16   
3333894  156         155  VLS+  Village 6 IUT     1               16   
3333895  156         155  VLS+  Village 6 IUT     1               15   
3333896  156         155  VLS+  Village 6 IUT     1               15   
3333897  156         155  VLS+  Village 6 IUT     1               15   
3333898  156         155  VLS+  Village 6 IUT     1               14   
3333899  156         155  VLS+  Village 6 IUT     1               14   
3333900  156         155  VLS+  Village 6 IUT     1               14   
3333901  156         155  VLS+  Village 6 IUT     1               14   
3333902  156         155  VLS+  Village 6 IUT     1               14   
3333903  156         155  VLS+  Village 6 IUT     1               14   
3333904  156         155  VLS+  Village 6 IUT     1               14   
3333905  156         155  VLS+  Village 6 IUT     1               14   
3333906  156         155  VLS+  Village 6 IUT     1               14   
3333907  156         155  VLS+  Village 6 IUT     1               14   
3333908  156         155  VLS+  Village 6 IUT     1               14   
3333909  156         155  VLS+  Village 6 IUT     1               14   
3333910  156         155  VLS+  Village 6 IUT     1               14   
3333911  156         155  VLS+  Village 6 IUT     1               14   
3333912  156         155  VLS+  Village 6 IUT     1               14   
3333913  156         155  VLS+  Village 6 IUT     1               14   
3333914  156         155  VLS+  Village 6 IUT     1               14   
3333915  156         155  VLS+  Village 6 IUT     1               14   
3333916  156         155  VLS+  Village 6 IUT     1               14   
3333917  156         155  VLS+  Village 6 IUT     1               14   
3333918  156         155  VLS+  Village 6 IUT     1               14   
3333919  156         155  VLS+  Village 6 IUT     1               15   
3333920  156         155  VLS+  Village 6 IUT     1               15   
3333921  156         155  VLS+  Village 6 IUT     1               15   
3333922  156         155  VLS+  Village 6 IUT     1               15   
3333923  156         155  VLS+  Village 6 IUT     1               15   
3333924  156         155  VLS+  Village 6 IUT     1               15   
3333925  156         155  VLS+  Village 6 IUT     1               15   
3333926  156         155  VLS+  Village 6 IUT     1               15   
3333927  156         155  VLS+  Village 6 IUT     1               15   
3333928  156         155  VLS+  Village 6 IUT     1               15   
3333929  156         155  VLS+  Village 6 IUT     1               15   
3333930  156         155  VLS+  Village 6 IUT     1               15   
3333931  156         155  VLS+  Village 6 IUT     1               15   
3333932  156         155  VLS+  Village 6 IUT     1               15   
3333933  156         155  VLS+  Village 6 IUT     1               15   
3333934  156         155  VLS+  Village 6 IUT     1               15   
3333935  156         155  VLS+  Village 6 IUT     1               15   
3333936  156         155  VLS+  Village 6 IUT     1               15   
3333937  156         155  VLS+  Village 6 IUT     1               16   
3333938  156         155  VLS+  Village 6 IUT     1               16   
3333939  156         155  VLS+  Village 6 IUT     1               16   
3333940  156         155  VLS+  Village 6 IUT     1               16   
3333941  156         155  VLS+  Village 6 IUT     1               16   

         available_bike                date  transactions_out  \
3333892               7 2017-07-25 09:30:04               0.0   
3333893               8 2017-07-25 09:40:03               0.0   
3333894               8 2017-07-25 09:45:04               0.0   
3333895               9 2017-07-25 09:55:04               0.0   
3333896    

In [55]:
activite['seconde'] = activite.date.dt.second

In [58]:
activite.tail(15)

gid  station_id type    name state  available_stand  available_bike  \
3761865  176         174  VLS  Darwin     1                2              18   
3761866  176         174  VLS  Darwin     1                2              18   
3761867  176         174  VLS  Darwin     1                2              18   
3761868  176         174  VLS  Darwin     1                1              19   
3761869  176         174  VLS  Darwin     1                1              19   
3761870  176         174  VLS  Darwin     1                0              20   
3761871  176         174  VLS  Darwin     1                0              20   
3761872  176         174  VLS  Darwin     1                1              19   
3761873  176         174  VLS  Darwin     1                1              19   
3761874  176         174  VLS  Darwin     1                1              19   
3761875  176         174  VLS  Darwin     1                1              19   
3761876  176         174  VLS  Darwin     1                0              20   
3761877  176         174  VLS  Darwin     1                0              20   
3761878  176         174  VLS  Darwin     1                0              20   
3761879  176         174  VLS  Darwin     1                0              20   

                       date  transactions_out  \
3761865 2017-09-26 13:49:04               0.0   
3761866 2017-09-26 13:54:04               0.0   
3761867 2017-09-26 13:59:03               0.0   
3761868 2017-09-26 14:04:05               0.0   
3761869 2017-09-26 14:09:04               0.0   
3761870 2017-09-26 14:14:04               0.0   
3761871 2017-09-26 14:19:03               0.0   
3761872 2017-09-26 14:24:04               1.0   
3761873 2017-09-26 14:29:05               0.0   
3761874 2017-09-26 14:34:03               0.0   
3761875 2017-09-26 14:39:02               0.0   
3761876 2017-09-26 14:44:05               0.0   
3761877 2017-09-26 14:49:05               0.0   
3761878 2017-09-26 14:54:04               0.0   
3761879 2017-09-26 14:59:04               0.0   

         consecutive_no_transactions_out  seconde  
3761865                               11        4  
3761866                               12        4  
3761867                               13        3  
3761868                               14        5  
3761869                               15        4  
3761870                               16        4  
3761871                               17        3  
3761872                                1        4  
3761873                                2        5  
3761874                                3        3  
3761875                                4        2  
3761876                                5        5  
3761877                                6        5  
3761878                                7        4  
3761879                                8        4